# Preprocessing Data

## Import Libraries

In [1]:
import os
import librosa
import json
import math
from sklearn.decomposition import PCA

C:\Users\ASUSROG\anaconda3\lib\site-packages\paramiko\transport.py:219: CryptographyDeprecationWarning: Blowfish has been deprecated
  "class": algorithms.Blowfish,


## Define Functions

In [ ]:
# Function to load dataset and extract MFCCs with segemnts
def extract_mfcc_seg(name, path, n_mfcc=13, n_fft=2048, hop_length=512, num_segments=5):
    
    # Make a dictionary to store the data
    data = {
        'mfcc': [],
        'label':[]
    }
    
    # Loop through the folders
    for dirpath, dirnames, filenames in os.walk(path):
        
        # Process audio files
        for file in filenames:
            
            # Check file type
            if file.endswith('.wav'):
                
                # Save the semantic label
                label = get_label(name, file)
                
                #print("\nProcessing {} from: {}".format(semantic_label, dirpath))
                
                if label is not None:

                    # Load audio file
                    file_path = os.path.join(dirpath, file)
                    signal, sr = librosa.load(file_path, sr=4000)

                    # Calculations
                    duration = len(signal) / sr
                    samples_per_track = 4000 / duration
                    samples_per_segments = int(samples_per_track / num_segments)
                    expected_mffc_amount = math.ceil(samples_per_segments / hop_length)

                    # Process segments and extract MFCC
                    for s in range(num_segments):
                        start_sample = samples_per_segments * s
                        finish_sample = start_sample + samples_per_segments

                        # Extract MFCC
                        mfcc = librosa.feature.mfcc(y=signal[start_sample:finish_sample],
                                                    sr=sr,
                                                    n_mfcc=n_mfcc,
                                                    n_fft=n_fft,
                                                    hop_length=hop_length
                                                   )
                        mfcc = mfcc.T

                        # Store the MFCC
                        if len(mfcc) == expected_mffc_amount:
                            data['mfcc'].append(mfcc.tolist())
                            data['label'].append(label)
                            print("{}\n{}, segment:{}".format(label, mfcc, s))
                
    return data

In [2]:
# Function to load dataset and extract MFCCs without segments
def extract_mfcc(name, path, n_mfcc=13, n_fft=2048, sr=44100):
    
    # Make a dictionary to store the data
    data = {
        'mfcc': [],
        'label':[]
    }
    
    # Loop through the folders
    for dirpath, dirnames, filenames in os.walk(path):
        
        # Process audio files
        for file in filenames:
            
            # Check file type
            if file.endswith('.wav'):
                
                # Save the semantic label
                label = get_label(name, file)
                
                if label is not None:
                    # Load audio file
                    file_path = os.path.join(dirpath, file)
                    signal, sr = librosa.load(file_path, sr=sr)

                    # Extract MFCC for the entire audio file
                    mfcc = librosa.feature.mfcc(y=signal,
                                                sr=sr,
                                                n_mfcc=n_mfcc,
                                                n_fft=n_fft,
                                               )
                    mfcc = mfcc.T

                    # Store the MFCC
                    data['mfcc'].append(mfcc.tolist())
                    data['label'].append(label)
                    print("{}\n{}".format(label, mfcc))
                    
    return data

In [19]:
# Function to load dataset and extract MFCCs without segments
def extract_spectrogram_with_pca(name, path, sr=44100, n_components=50):
    
    # Make a dictionary to store the data
    data = {
        'spectrogram': [],
        'label': []
    }
    
    # Loop through the folders
    for dirpath, dirnames, filenames in os.walk(path):
        
        # Process audio files
        for file in filenames:
            
            # Check file type
            if file.endswith('.wav'):
                
                # Save the semantic label
                label = get_label(name, file)
                
                if label is not None:
                    # Load audio file
                    file_path = os.path.join(dirpath, file)
                    signal, sr = librosa.load(file_path, sr=sr)

                    # Extract spectrogram for the entire audio file
                    spectrogram = librosa.stft(signal)

                    # Convert to dB scale
                    spectrogram_db = librosa.amplitude_to_db(np.abs(spectrogram))

                    # Perform PCA for dimensionality reduction
                    flattened_spectrogram = spectrogram_db.flatten().reshape(1, -1)
                    pca = PCA(n_components=n_components)
                    reduced_spectrogram = pca.fit_transform(flattened_spectrogram)

                    # Store the reduced spectrogram
                    data['spectrogram'].append(reduced_spectrogram.tolist())
                    data['label'].append(label)
                    print("{}\n{}".format(label, reduced_spectrogram))
                    
    return data


In [4]:
# Function to label data
def get_label(name, data_label):
    
    # Check the dataset of the label
    if name == 'ravdess':
        label = data_label[7]
        label_name = {
            '1': 'neutral',
            '2': 'calm',
            '3': 'happy',
            '4': 'sad',
            '5': 'angry',
            '6': 'fearful',
            '7': 'disgust',
            '8': 'surprised'
        }
        
    elif name == 'crema':
        label = data_label.split('_')[2]
        label_name = {
            'ANG': 'angry',
            'DIS': 'disgust',
            'FEA': 'fearful',
            'HAP': 'happy',
            'NEU': 'neutral',
            'SAD': 'sad'
        }
        
    elif name == 'savee':
        label = data_label[0]
        if label == 's':
            label = data_label[0:2]
            
        label_name = {
            'a': 'angry',
            'd': 'disgust',
            'f': 'fearful',
            'h': 'happy',
            'n': 'neutral',
            'sa': 'sad',
            'su': 'surprised'
        }
        
    elif name == 'tess':
        label = data_label.split('_')[2]
        label_name = {
            'angry.wav': 'angry',
            'disgust.wav': 'disgust',
            'fear.wav': 'fearful',
            'happy.wav': 'happy',
            'neutral.wav': 'neutral',
            'ps.wav': 'surprised',
            'sad.wav': 'sad'
        }
    
    """"
    Encode all labels
    # Encode the label
    label_encoding = {
        'neutral': 0,
        'calm': 1,
        'happy': 2,
        'sad': 3,
        'angry': 4,
        'fearful': 5,
        'disgust': 6,
        'surprised': 7
    }
    """
    
    
    # Encode only 6 label
    label_encoding = {
        'neutral': 0,
        'happy': 1,
        'sad': 2,
        'angry': 3,
        'fearful': 4,
        'disgust': 5,
    }
    
    semantic_label = label_name.get(label)
    num_label = label_encoding.get(semantic_label)
    
    return num_label

## RAVDESS Dataset

In [ ]:
## Path of the dataset
ravdess_path = f"{os.getcwd()}/ravdess"

# Load data
ravdess_data = extract_mfcc('ravdess', ravdess_path)

In [ ]:
print(ravdess_data['mfcc'][18], ravdess_data['label'][18])
len(ravdess_data['mfcc'])

In [ ]:
## Path of the dataset
ravdess_path = f"{os.getcwd()}/ravdess"
ravdess_data = extract_spectogram('ravdess', ravdess_path)

In [17]:
print(ravdess_data['spectogram'][18], ravdess_data['label'][18])
len(ravdess_data['spectogram'][0])

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



1025

## CREMA_D Dataset

In [5]:
# Path of the dataset
crema_path = f"{os.getcwd()}/crema_d"

# Load data
crema_data = extract_mfcc('crema', crema_path)

3
[[-622.7939        0.            0.         ...    0.
     0.            0.        ]
 [-622.7939        0.            0.         ...    0.
     0.            0.        ]
 [-601.03357      28.965769     24.086872   ...    0.98357797
     1.3900303     1.8366205 ]
 ...
 [-498.82394     114.57364      34.86152    ...   -2.639728
    -3.5579681     3.7444358 ]
 [-505.29803     112.91365      36.319344   ...   -4.523143
    -6.767444     -2.7266757 ]
 [-539.6904       91.26134      43.758865   ...   -3.8015459
    -9.049277     -8.248456  ]]
5
[[-555.6428     138.06932     15.91585   ...   -2.8668761   -3.6638908
    -1.5535455]
 [-534.7079     146.9122       8.733688  ...   -9.122511    -5.1084723
    -2.7626615]
 [-537.52167    144.93854     14.263882  ...   -9.91844     -1.7697804
    -2.560618 ]
 ...
 [-530.12384    155.17621     20.173084  ...   -8.782604    -2.4065542
    -1.0159962]
 [-538.8364     149.36394     18.314404  ...   -8.8197155   -3.8509803
    -5.2981853]
 [-586.94495 

1
[[-5.1117487e+02  1.3455569e+02  1.7995148e+01 ... -1.4301630e+00
  -3.2830629e+00 -8.9255753e+00]
 [-5.1658826e+02  1.4116432e+02  1.9907890e+01 ... -2.3761392e+00
  -3.5679129e-01 -5.3415375e+00]
 [-5.2104419e+02  1.3717459e+02  1.9095680e+01 ... -2.7942829e+00
  -4.2802358e+00 -5.5241909e+00]
 ...
 [-5.1996283e+02  1.4215666e+02  2.6563389e+01 ... -9.0204973e+00
  -2.0054581e+00  3.9391100e-02]
 [-5.0808340e+02  1.4720181e+02  1.8869631e+01 ... -5.9402018e+00
  -6.9001681e-01 -1.4441092e+00]
 [-5.2074780e+02  1.3896750e+02  1.2981478e+01 ... -7.4370658e-01
   1.5579898e+00 -1.8367764e-01]]
1
[[-5.3327539e+02  1.0720328e+02  4.6859497e+01 ... -9.4183341e-02
  -3.0667704e-01 -6.1311808e+00]
 [-5.0854709e+02  1.1683516e+02  3.5779549e+01 ... -1.1069075e+00
  -2.8277526e+00 -5.8419018e+00]
 [-5.0388913e+02  1.2058514e+02  3.5243313e+01 ... -1.0056491e+01
  -8.2654877e+00 -2.8310730e+00]
 ...
 [-4.9881445e+02  1.2216751e+02  3.5794445e+01 ... -6.7851734e+00
  -7.6474071e+00 -8.3304539e

0
[[-539.91925     129.0192       14.831127   ...   -2.4714851
     3.0091653    -9.216082  ]
 [-526.7106      142.0668       17.155136   ...   -5.1500297
    -5.942108     -9.15994   ]
 [-531.2012      139.0206       17.024973   ...   -4.8790164
    -5.5999575    -3.7133727 ]
 ...
 [-533.47894     136.7096       12.796766   ...   -9.027507
    -5.1698685    -7.4915333 ]
 [-530.7056      147.68628      22.940182   ...   -6.008108
    -2.0228674    -0.62288415]
 [-569.6414      134.42578      42.120575   ...   -5.3524504
     0.65652895    4.8096113 ]]
2
[[-572.838      173.88326     -0.8109944 ...  -11.333145    -5.468999
    -4.2641034]
 [-563.67035    185.8272      -9.696856  ...  -14.378881    -1.495564
    -5.1977224]
 [-560.6503     190.82304     -6.461862  ...  -10.746788    -1.8286498
    -5.681122 ]
 ...
 [-567.3626     185.34236     -9.187738  ...   -9.883171    -1.53686
     3.9833422]
 [-587.4909     177.06258    -10.042971  ...  -12.51709     -6.004494
     1.6150813]
 [-66

4
[[-5.32273254e+02  1.00196609e+02  3.86968842e+01 ... -6.19929504e+00
  -6.48167801e+00  1.89743924e+00]
 [-5.11955536e+02  1.11304718e+02  3.36822433e+01 ... -9.17033195e+00
  -4.76318216e+00  3.17701191e-01]
 [-5.04603455e+02  1.21336342e+02  4.03265724e+01 ... -7.92328358e+00
  -5.87587833e+00 -2.58300114e+00]
 ...
 [-5.08081207e+02  1.20007774e+02  4.04746094e+01 ... -4.78157234e+00
  -1.01810198e+01 -1.34583645e+01]
 [-5.16946411e+02  1.18653961e+02  4.82897644e+01 ...  7.63159180e+00
   4.61037159e+00 -5.97849274e+00]
 [-5.40368347e+02  1.06564316e+02  5.42432785e+01 ...  9.16225624e+00
   8.55179310e+00 -1.71862841e+00]]
1
[[-4.69342987e+02  1.29492523e+02  1.24472141e+01 ... -1.49360085e+00
   5.75326729e+00 -1.26833057e+00]
 [-4.89858307e+02  1.29829285e+02  1.64758339e+01 ... -8.00353622e+00
  -7.90658712e-01 -1.39366937e+00]
 [-5.03205719e+02  1.25955414e+02  2.34705353e+01 ... -6.17015648e+00
  -4.70758533e+00  5.46938837e-01]
 ...
 [-5.01717529e+02  1.30654999e+02  2.411

2
[[-5.2358600e+02  1.3629851e+02  2.4398623e+00 ... -7.3603125e+00
  -5.9292283e+00 -7.9184895e+00]
 [-5.3713959e+02  1.6192191e+02  3.6165446e-01 ... -1.0405374e+01
  -4.1730595e+00 -4.1257963e+00]
 [-5.4915625e+02  1.6615544e+02  7.4170051e+00 ... -1.3638464e+01
  -5.2172537e+00 -7.1049442e+00]
 ...
 [-5.4356580e+02  1.6282504e+02 -7.6531935e+00 ... -6.7931271e+00
   5.0886078e+00  5.4783769e+00]
 [-5.3837866e+02  1.6840668e+02 -7.7294359e+00 ... -9.7488613e+00
   2.2318702e+00  3.6445789e+00]
 [-5.5344348e+02  1.7108670e+02  4.5516424e+00 ... -7.8367152e+00
   2.3119764e+00  3.0468919e+00]]
3
[[-4.97743164e+02  1.32557556e+02  2.27586818e+00 ...  1.80447817e+00
   3.01325703e+00 -8.05112457e+00]
 [-5.00001404e+02  1.38470215e+02  2.79485166e-01 ... -2.24187899e+00
   2.75042057e+00 -5.23859310e+00]
 [-5.06621033e+02  1.39915436e+02  6.89590979e+00 ... -2.38489270e+00
  -4.45712328e-01 -3.18318081e+00]
 ...
 [-5.09531616e+02  1.51335236e+02  2.24894238e+01 ... -1.12917690e+01
  -1.2

...

5
[[-5.9551093e+02  1.2890573e+02  4.2624069e+01 ... -3.6738701e+00
   6.9444065e+00  6.3244181e+00]
 [-5.7407867e+02  1.3966354e+02  3.7832230e+01 ... -4.6046257e+00
   2.5176883e+00  1.5775783e+00]
 [-5.7448975e+02  1.3837531e+02  3.5391563e+01 ... -6.0914125e+00
  -1.4365168e+00  1.5565945e+00]
 ...
 [-5.7394836e+02  1.3782120e+02  3.0734066e+01 ... -3.1623235e-01
   3.0054998e-01 -4.0069714e+00]
 [-5.7138477e+02  1.3924741e+02  2.6514854e+01 ... -3.1545906e+00
  -1.7541764e+00 -2.1905441e+00]
 [-5.6361981e+02  1.5102802e+02  2.1853813e+01 ... -3.6552753e+00
  -1.3237138e+00  3.9766837e-02]]
4
[[-5.51059570e+02  1.11674377e+02  2.87970772e+01 ... -1.42848969e+01
  -5.35665941e+00 -7.95104790e+00]
 [-5.40466064e+02  1.17544159e+02  2.51036358e+01 ... -1.07448997e+01
  -2.74636984e-01 -3.30351257e+00]
 [-5.44491699e+02  1.18191940e+02  2.72516556e+01 ... -5.90909290e+00
   6.45195866e+00  5.79417324e+00]
 ...
 [-5.59320251e+02  1.22018936e+02  4.80378380e+01 ...  4.86427248e-01
  -1.0

1
[[-5.25806030e+02  1.12911346e+02  2.96779099e+01 ... -2.74221992e+00
   1.10607982e+00 -4.83836353e-01]
 [-5.16327881e+02  1.16194588e+02  2.76617126e+01 ...  1.29979491e-01
   9.50316191e-01 -1.89635324e+00]
 [-5.17393555e+02  1.14656036e+02  2.63019581e+01 ...  1.58397543e+00
  -1.86599576e+00 -4.79584503e+00]
 ...
 [-5.52934265e+02  1.09005775e+02  6.12532043e+01 ...  3.45103168e+00
   4.60353851e+00  3.19414544e+00]
 [-5.67058777e+02  1.03170547e+02  6.24804230e+01 ...  5.28873158e+00
   1.03150682e+01  6.91019773e+00]
 [-6.01928833e+02  6.86501007e+01  5.14126511e+01 ...  6.12740898e+00
   1.01368895e+01  1.08525276e+01]]
0
[[-5.9012451e+02  1.3992273e+02  2.8671803e+01 ... -1.1711402e+00
  -4.8431808e-01 -5.8721167e-01]
 [-5.7823364e+02  1.4765536e+02  2.7174309e+01 ...  9.3699712e-01
   3.2301230e+00  1.6844397e+00]
 [-5.7834125e+02  1.4769075e+02  2.6839666e+01 ...  5.4929543e+00
   3.7215667e+00  7.9326153e-01]
 ...
 [-5.7755579e+02  1.4900037e+02  2.6316145e+01 ...  5.7938

2
[[-5.4085254e+02  1.3129797e+02  1.2971241e+01 ... -4.7559762e+00
   1.4358482e+00 -3.1441998e-01]
 [-5.6204279e+02  1.4748630e+02  2.2481131e+01 ... -7.6085520e+00
   1.9118165e+00 -3.0334630e+00]
 [-5.8057135e+02  1.4224707e+02  3.0982494e+01 ... -4.6143475e+00
   1.5818005e+00  1.3651112e+00]
 ...
 [-5.7189899e+02  1.5038464e+02  2.9344231e+01 ... -2.4743252e+00
  -1.0641723e+00  1.3291061e+00]
 [-5.7116504e+02  1.5114426e+02  2.9641018e+01 ... -6.1386976e+00
   7.5685382e-01  3.0392206e+00]
 [-5.9439893e+02  1.4095325e+02  3.0810982e+01 ... -5.2593117e+00
   4.9534231e-01  2.4968505e+00]]
3
[[-5.17143799e+02  1.22204094e+02  2.58574791e+01 ...  5.30100250e+00
   7.39053059e+00 -1.43409669e+00]
 [-5.39600342e+02  1.16608841e+02  4.30855408e+01 ...  5.83488703e+00
   4.54652834e+00  9.51822400e-02]
 [-5.58541687e+02  1.11531319e+02  5.83464928e+01 ...  4.12091923e+00
   1.53513104e-01 -2.02125120e+00]
 ...
 [-5.58678833e+02  1.06221046e+02  4.87296600e+01 ... -4.75074148e+00
   1.7

5
[[-5.62042175e+02  1.27940269e+02  3.42138138e+01 ...  2.67138290e+00
   2.38503933e+00  1.18398094e+00]
 [-5.62954590e+02  1.30504089e+02  4.33422012e+01 ...  1.75701928e+00
   1.21832657e+00  2.84676814e+00]
 [-5.75553589e+02  1.21126564e+02  4.25973396e+01 ... -8.15321565e-01
  -3.46532416e+00 -5.19851208e-01]
 ...
 [-5.65265259e+02  1.34057007e+02  4.74484482e+01 ...  4.89872169e+00
   6.77052689e+00  3.26803207e+00]
 [-5.76495483e+02  1.29566467e+02  5.38165512e+01 ...  2.59201503e+00
   3.90935016e+00 -1.67562711e+00]
 [-6.09002502e+02  1.16053024e+02  6.58551788e+01 ... -1.59281778e+00
  -2.91581154e-02 -5.17229915e-01]]
4
[[-533.60223    118.05705     35.76351   ...    1.6672912    2.958774
    -0.9624888]
 [-545.0242     113.69149     44.586876  ...    4.695296     1.5157363
    -1.1684498]
 [-553.21155    109.95053     48.816383  ...    1.8298088   -5.7340536
    -4.963602 ]
 ...
 [-557.66656    104.61749     43.8575    ...   -2.593627    -4.694823
    -2.4006152]
 [-515.98

1
[[-593.05975    120.61459     33.926865  ...    0.6295599    5.468548
     9.120735 ]
 [-576.97894    126.65962     29.226524  ...   -4.244645     1.5247546
     4.030575 ]
 [-576.8487     127.54091     26.282257  ...   -4.2546372    1.816914
     7.685629 ]
 ...
 [-547.9605     132.1479      22.724476  ...   -1.4304898   13.691021
     2.8540394]
 [-542.139      139.7388      14.936987  ...   -6.1889825    5.1391954
     3.1450386]
 [-536.00726    146.08936      6.0543356 ...   -5.982458     4.5850124
     5.7846947]]
0
[[-5.9317365e+02  1.1435446e+02  4.1711433e+01 ... -1.9380882e-01
   4.9558082e-01  7.4775009e+00]
 [-5.7187854e+02  1.2515047e+02  3.7558998e+01 ... -6.4826260e+00
  -2.3122895e+00  3.9673266e+00]
 [-5.7436975e+02  1.2335834e+02  4.0474854e+01 ... -2.4957469e+00
  -2.4407172e+00  1.7537555e+00]
 ...
 [-5.6534784e+02  1.3148810e+02  4.0695652e+01 ... -1.5314407e+00
  -8.9988585e+00 -9.3645096e+00]
 [-5.6068829e+02  1.3760007e+02  4.2273315e+01 ... -2.3229361e+00
  -4

In [ ]:
print(crema_data['mfcc'][7], crema_data['label'][7])
len(crema_data['mfcc'])

In [ ]:
crema_path = f"{os.getcwd()}/crema_d"
crema_data = extract_spectogram('crema', crema_path)

In [ ]:
print(crema_data['mfcc'][7], crema_data['label'][7])
len(crema_data['mfcc'])

## SAVEE Dataset

In [ ]:
# Path of the dataset
savee_path = f"{os.getcwd()}/savee"

# Load data
savee_data = extract_mfcc('savee', savee_path)

In [ ]:
print(savee_data['mfcc'][7], savee_data['label'][7])
len(savee_data['mfcc'])

In [ ]:
savee_path = f"{os.getcwd()}/savee"
savee_data = extract_spectogram('savee', savee_path)

In [ ]:
print(savee_data['mfcc'][7], savee_data['label'][7])
len(savee_data['mfcc'])

## TESS Dataset

In [ ]:
# Path of the dataset
tess_path = f"{os.getcwd()}/tess"

# Load data
tess_data = extract_mfcc('tess', tess_path)

In [ ]:
print(tess_data['mfcc'][7], tess_data['label'][7])
len(tess_data['mfcc'])

In [ ]:
tess_path = f"{os.getcwd()}/tess"
tess_data = extract_spectogram('tess', tess_path)

In [ ]:
print(tess_data['mfcc'][7], tess_data['label'][7])
len(tess_data['mfcc'])

## Augmented RAVDESS Dataset

In [ ]:
# Path of the dataset
aug_path = f"{os.getcwd()}/augmented_data"

# Load data
aug_data = extract_mfcc('ravdess', aug_path)

In [ ]:
print(aug_data['mfcc'][7], aug_data['label'][7])
len(aug_data['mfcc'])

## Combine Data

In [6]:
# Dictionary to save all the data
data = {
    'mfcc': [],
    'label': []
}

print(len(data['mfcc']), len(data['label']))

0 0


In [ ]:
# Add ravdess data
data['mfcc'].extend(ravdess_data['mfcc'])
data['label'].extend(ravdess_data['label'])

print(len(data['mfcc']), len(data['label']))

In [7]:
# Add crema data
data['mfcc'].extend(crema_data['mfcc'])
data['label'].extend(crema_data['label'])

print(len(data['mfcc']), len(data['label']))

7442 7442


In [ ]:
# Add savee data
data['mfcc'].extend(savee_data['mfcc'])
data['label'].extend(savee_data['label'])

print(len(data['mfcc']), len(data['label']))

In [ ]:
# Add tess data
data['mfcc'].extend(tess_data['mfcc'])
data['label'].extend(tess_data['label'])

print(len(data['mfcc']), len(data['label']))

In [ ]:
# Add augmented data
data['mfcc'].extend(aug_data['mfcc'])
data['label'].extend(aug_data['label'])

print(len(data['mfcc']), len(data['label']))

In [ ]:
# Dictionary to save all the data
data = {
    'spectogram': [],
    'label': []
}

data['spectogram'].extend(ravdess_data['spectogram'])
data['label'].extend(ravdess_data['label'])

data['spectogram'].extend(crema_data['spectogram'])
data['label'].extend(crema_data['label'])

data['spectogram'].extend(savee_data['spectogram'])
data['label'].extend(savee_data['label'])

data['spectogram'].extend(aug_data['spectogram'])
data['label'].extend(aug_data['label'])

## Ouput

In [8]:
def save_json(json_path, data):
    with open(json_path, 'w') as f:
        json.dump(data, f, indent=4)

In [9]:
# Path of the json file
json_path = 'crema-data.json'

# Ouput json file
save_json(json_path, data)